In [1]:
# -*- coding: utf-8 -*-
# เรียกใช้งานโมดูล
file_name="data"
import codecs
from pythainlp.tokenize import word_tokenize
#import deepcut
from pythainlp.tag import pos_tag
from nltk.tokenize import RegexpTokenizer
import glob
import nltk
import re
# thai cut
thaicut="newmm"
from sklearn_crfsuite import scorers,metrics
from sklearn.metrics import make_scorer
from sklearn.model_selection import cross_validate,train_test_split
import sklearn_crfsuite
from pythainlp.corpus.common import thai_stopwords
stopwords = list(thai_stopwords())

In [2]:
import dill
with open('datatrain.data', 'rb') as file:
 datatofile = dill.load(file)

In [3]:
t=[]

In [4]:
def isThai(chr):
 cVal = ord(chr)
 if(cVal >= 3584 and cVal <= 3711):
  return True
 return False
def isThaiWord(word):
 t=True
 for i in word:
  l=isThai(i)
  if l!=True and i!='.':
   t=False
   break
 return t

def is_stopword(word):
    return word in stopwords
def is_s(word):
    if word == " " or word =="\t" or word=="":
        return True
    else:
        return False

def lennum(word,num):
    if len(word)==num:
        return True
    return False
def doc2features(doc, i):
    word = doc[i][0]
    postag = doc[i][1]
    # Features from current word
    features={
        'word.word': word,
        'word.stopword': is_stopword(word),
        'word.isthai':isThaiWord(word),
        'word.isspace':word.isspace(),
        'postag':postag,
        'word.isdigit()': word.isdigit()
    }
    if word.isdigit() and len(word)==5:
        features['word.islen5']=True
    if i > 0:
        prevword = doc[i-1][0]
        postag1 = doc[i-1][1]
        features['word.prevword'] = prevword
        features['word.previsspace']=prevword.isspace()
        features['word.previsthai']=isThaiWord(prevword)
        features['word.prevstopword']=is_stopword(prevword)
        features['word.prepostag'] = postag1
        features['word.prevwordisdigit'] = prevword.isdigit()
    else:
        features['BOS'] = True # Special "Beginning of Sequence" tag
    # Features from next word
    if i < len(doc)-1:
        nextword = doc[i+1][0]
        postag1 = doc[i+1][1]
        features['word.nextword'] = nextword
        features['word.nextisspace']=nextword.isspace()
        features['word.nextpostag'] = postag1
        features['word.nextisthai']=isThaiWord(nextword)
        features['word.nextstopword']=is_stopword(nextword)
        features['word.nextwordisdigit'] = nextword.isdigit()
    else:
        features['EOS'] = True # Special "End of Sequence" tag
    return features

def extract_features(doc):
    return [doc2features(doc, i) for i in range(len(doc))]

def get_labels(doc):
    return [tag for (token,postag,tag) in doc]

In [5]:
X_data = [extract_features(doc) for doc in datatofile]
y_data = [get_labels(doc) for doc in datatofile]

In [6]:
X_data[0]

[{'word.word': 'http',
  'word.stopword': False,
  'word.isthai': False,
  'word.isspace': False,
  'postag': 'NOUN',
  'word.isdigit()': False,
  'BOS': True,
  'word.nextword': '://',
  'word.nextisspace': False,
  'word.nextpostag': 'NOUN',
  'word.nextisthai': False,
  'word.nextstopword': False,
  'word.nextwordisdigit': False},
 {'word.word': '://',
  'word.stopword': False,
  'word.isthai': False,
  'word.isspace': False,
  'postag': 'NOUN',
  'word.isdigit()': False,
  'word.prevword': 'http',
  'word.previsspace': False,
  'word.previsthai': False,
  'word.prevstopword': False,
  'word.prepostag': 'NOUN',
  'word.prevwordisdigit': False,
  'word.nextword': 'www',
  'word.nextisspace': False,
  'word.nextpostag': 'NOUN',
  'word.nextisthai': False,
  'word.nextstopword': False,
  'word.nextwordisdigit': False},
 {'word.word': 'www',
  'word.stopword': False,
  'word.isthai': False,
  'word.isspace': False,
  'postag': 'NOUN',
  'word.isdigit()': False,
  'word.prevword': '://',

In [7]:
j=""
for i in datatofile:
    t=""
    for a,b,c in i:
        t+=a.encode("utf-8").decode()
    j+=t+"\n"

In [8]:
datatofile[0]

[('http', 'NOUN', 'B-URL'),
 ('://', 'NOUN', 'I-URL'),
 ('www', 'NOUN', 'I-URL'),
 ('.', 'PUNCT', 'I-URL'),
 ('bangkokhealth', 'NOUN', 'I-URL'),
 ('.', 'PUNCT', 'I-URL'),
 ('com', 'NOUN', 'I-URL'),
 ('/', 'PUNCT', 'I-URL'),
 ('healthnews', 'NOUN', 'I-URL'),
 ('_', 'NOUN', 'I-URL'),
 ('htdoc', 'NOUN', 'I-URL'),
 ('/', 'PUNCT', 'I-URL'),
 ('healthnews', 'NOUN', 'I-URL'),
 (' ', 'PUNCT', 'I-URL'),
 ('_', 'NOUN', 'I-URL'),
 (' ', 'PUNCT', 'I-URL'),
 ('detail', 'NOUN', 'I-URL'),
 ('.', 'PUNCT', 'I-URL'),
 ('asp', 'NOUN', 'I-URL'),
 ('?', 'PUNCT', 'I-URL'),
 ('Number', 'NOUN', 'I-URL'),
 ('=', 'PUNCT', 'I-URL'),
 ('10506', 'NUM', 'I-URL')]

In [9]:
trainer=[]
train_data = zip(X_data, y_data)
# ตามคำแนะนำของปศุสัตว์
for xseq, yseq in train_data:
    trainer.append((xseq, yseq))

In [20]:
aa={'word.word': 'ไป', 'word.stopword': True, 'word.isthai': True, 'word.isspace': False, 'postag': 'AUX', 'word.isdigit()': False, 'word.prevword': 'เก็บ', 'word.previsspace': False, 'word.previsthai': True, 'word.prevstopword': True, 'word.prepostag': 'VERB', 'word.prevwordisdigit': False, 'EOS': True}

In [21]:
i=0
while i<len(X_data):
    if aa in X_data[i]:
        print(i)
    i+=1

6210


In [14]:
del X_data[1079]
del y_data[1079]

In [22]:
i=6210#4789
del X_data[i]
del y_data[i]

In [23]:
crf2 = sklearn_crfsuite.CRF(
    algorithm='lbfgs',
    c1=0.1,
    c2=0.1,
    max_iterations=500,
    all_possible_transitions=True,
    model_filename=file_name+".model",verbose=True
)
crf2.fit(X_data, y_data);




loading training data to CRFsuite:   0%|          | 0/6284 [00:00<?, ?it/s]


loading training data to CRFsuite:   0%|          | 23/6284 [00:00<00:28, 220.29it/s]


loading training data to CRFsuite:   1%|          | 49/6284 [00:00<00:27, 228.79it/s]

[{'word.word': 'http', 'word.stopword': False, 'word.isthai': False, 'word.isspace': False, 'postag': 'NOUN', 'word.isdigit()': False, 'BOS': True, 'word.nextword': '://', 'word.nextisspace': False, 'word.nextpostag': 'NOUN', 'word.nextisthai': False, 'word.nextstopword': False, 'word.nextwordisdigit': False}, {'word.word': '://', 'word.stopword': False, 'word.isthai': False, 'word.isspace': False, 'postag': 'NOUN', 'word.isdigit()': False, 'word.prevword': 'http', 'word.previsspace': False, 'word.previsthai': False, 'word.prevstopword': False, 'word.prepostag': 'NOUN', 'word.prevwordisdigit': False, 'word.nextword': 'www', 'word.nextisspace': False, 'word.nextpostag': 'NOUN', 'word.nextisthai': False, 'word.nextstopword': False, 'word.nextwordisdigit': False}, {'word.word': 'www', 'word.stopword': False, 'word.isthai': False, 'word.isspace': False, 'postag': 'NOUN', 'word.isdigit()': False, 'word.prevword': '://', 'word.previsspace': False, 'word.previsthai': False, 'word.prevstopword




loading training data to CRFsuite:   3%|▎         | 174/6284 [00:00<00:20, 303.06it/s]


loading training data to CRFsuite:   6%|▌         | 375/6284 [00:00<00:14, 406.42it/s]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




loading training data to CRFsuite:   8%|▊         | 518/6284 [00:00<00:11, 517.39it/s]


loading training data to CRFsuite:  10%|▉         | 626/6284 [00:00<00:10, 547.30it/s]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=

loading training data to CRFsuite:  59%|█████▉    | 3714/6284 [00:04<00:02, 888.15it/s] 


loading training data to CRFsuite:  61%|██████    | 3826/6284 [00:04<00:02, 883.74it/s]


loading training data to CRFsuite:  63%|██████▎   | 3931/6284 [00:04<00:02, 857.79it/s]IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)




loading training data to CRFsuite:  64%|██████▍   | 4029/6284 [00:05<00:03, 644.06it/s]


loading training data to CRFsuite:  65%|██████▌   | 4110/6284 [00:05<00:03, 588.11it/s]

[{'word.word': 'จาก', 'word.stopword': True, 'word.isthai': True, 'word.isspace': False, 'postag': 'ADP', 'word.isdigit()': False, 'BOS': True, 'word.nextword': 'การสำรวจ', 'word.nextisspace': False, 'word.nextpostag': 'NOUN', 'word.nextisthai': True, 'word.nextstopword': False, 'word.nextwordisdigit': False}, {'word.word': 'การสำรวจ', 'word.stopword': False, 'word.isthai': True, 'word.isspace': False, 'postag': 'NOUN', 'word.isdigit()': False, 'word.prevword': 'จาก', 'word.previsspace': False, 'word.previsthai': True, 'word.prevstopword': True, 'word.prepostag': 'ADP', 'word.prevwordisdigit': False, 'word.nextword': 'ของ', 'word.nextisspace': False, 'word.nextpostag': 'ADP', 'word.nextisthai': True, 'word.nextstopword': True, 'word.nextwordisdigit': False}, {'word.word': 'ของ', 'word.stopword': True, 'word.isthai': True, 'word.isspace': False, 'postag': 'ADP', 'word.isdigit()': False, 'word.prevword': 'การสำรวจ', 'word.previsspace': False, 'word.previsthai': True, 'word.prevstopword':




loading training data to CRFsuite:  67%|██████▋   | 4181/6284 [00:05<00:03, 619.83it/s]


loading training data to CRFsuite:  68%|██████▊   | 4276/6284 [00:05<00:02, 690.95it/s]


IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



5....6....7....8....9....10
Number of features: 61095
Seconds required: 0.569

L-BFGS optimization
c1: 0.100000
c2: 0.100000
num_memories: 6
max_iterations: 500
epsilon: 0.000010
stop: 10
delta: 0.000010
linesearch: MoreThuente
linesearch.max_iterations: 20

Iter 1   time=1.37  loss=453628.02 active=60745 feature_norm=1.00
Iter 2   time=1.52  loss=358374.40 active=60106 feature_norm=3.89
Iter 3   time=0.73  loss=293100.45 active=57750 feature_norm=3.29
Iter 4   time=2.17  loss=254383.43 active=58187 feature_norm=2.23
Iter 5   time=0.71  loss=226926.82 active=60458 feature_norm=2.94
Iter 6   time=0.70  loss=208794.33 active=60301 feature_norm=2.89
Iter 7   time=0.70  loss=205621.29 active=59198 feature_norm=3.35
Iter 8   time=0.71  loss=187114.30 active=60476 feature_norm=3.39
Iter 9   time=0.70  loss=179417.75 active=60589 feature_norm=3.73
Iter 10  time=0.70  loss=153247.25 active=58045 feature_norm=6.15
Iter 11  time=0.70  loss=141542.62 active=57780 feature_norm=6.68
Iter 12  time=0

Iter 139 time=0.70  loss=11621.41 active=30245 feature_norm=189.57
Iter 140 time=0.70  loss=11619.95 active=30260 feature_norm=189.56
Iter 141 time=0.71  loss=11618.84 active=30248 feature_norm=189.60
Iter 142 time=0.70  loss=11617.28 active=30245 feature_norm=189.58
Iter 143 time=0.71  loss=11616.02 active=30233 feature_norm=189.62
Iter 144 time=0.71  loss=11614.60 active=30243 feature_norm=189.60
Iter 145 time=0.70  loss=11613.66 active=30249 feature_norm=189.64
Iter 146 time=0.70  loss=11612.06 active=30241 feature_norm=189.62
Iter 147 time=0.72  loss=11611.00 active=30225 feature_norm=189.66
Iter 148 time=0.71  loss=11609.45 active=30230 feature_norm=189.64
Iter 149 time=0.72  loss=11608.57 active=30213 feature_norm=189.68
Iter 150 time=0.75  loss=11606.88 active=30201 feature_norm=189.67
Iter 151 time=0.70  loss=11605.87 active=30189 feature_norm=189.70
Iter 152 time=0.75  loss=11604.28 active=30174 feature_norm=189.69
Iter 153 time=0.71  loss=11603.52 active=30164 feature_norm=18

Iter 283 time=0.71  loss=11510.56 active=29550 feature_norm=188.94
Iter 284 time=0.71  loss=11509.88 active=29549 feature_norm=188.93
Iter 285 time=0.71  loss=11509.61 active=29557 feature_norm=188.93
Iter 286 time=0.71  loss=11509.00 active=29556 feature_norm=188.92
Iter 287 time=0.71  loss=11508.73 active=29543 feature_norm=188.92
Iter 288 time=0.71  loss=11508.20 active=29542 feature_norm=188.91
Iter 289 time=0.71  loss=11508.08 active=29540 feature_norm=188.91
Iter 290 time=0.71  loss=11507.34 active=29537 feature_norm=188.90
Iter 291 time=0.71  loss=11507.32 active=29534 feature_norm=188.90
Iter 292 time=0.71  loss=11506.47 active=29536 feature_norm=188.89
Iter 293 time=0.71  loss=11506.47 active=29531 feature_norm=188.89
Iter 294 time=0.76  loss=11505.69 active=29536 feature_norm=188.88
Iter 295 time=1.41  loss=11505.33 active=29539 feature_norm=188.88
Iter 296 time=0.70  loss=11504.95 active=29522 feature_norm=188.86
Iter 297 time=0.71  loss=11504.88 active=29521 feature_norm=18

Iter 406 time=1.43  loss=11472.50 active=29112 feature_norm=188.25
Iter 407 time=1.44  loss=11472.44 active=29106 feature_norm=188.24
Iter 408 time=1.43  loss=11472.14 active=29099 feature_norm=188.24
Iter 409 time=1.43  loss=11472.04 active=29095 feature_norm=188.23
Iter 410 time=1.44  loss=11471.79 active=29093 feature_norm=188.22
Iter 411 time=1.45  loss=11471.70 active=29094 feature_norm=188.22
Iter 412 time=1.43  loss=11471.43 active=29088 feature_norm=188.21
Iter 413 time=1.43  loss=11471.31 active=29089 feature_norm=188.20
Iter 414 time=1.44  loss=11471.09 active=29088 feature_norm=188.19
Iter 415 time=1.43  loss=11471.00 active=29088 feature_norm=188.19
Iter 416 time=1.45  loss=11470.76 active=29084 feature_norm=188.18
Iter 417 time=1.43  loss=11470.66 active=29080 feature_norm=188.17
Iter 418 time=1.43  loss=11470.48 active=29079 feature_norm=188.17
Iter 419 time=1.42  loss=11470.39 active=29079 feature_norm=188.17
Iter 420 time=1.42  loss=11470.22 active=29070 feature_norm=18